In [54]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from statsmodels.tsa.holtwinters import ExponentialSmoothing
from sklearn.metrics import mean_squared_error, mean_absolute_error
import os
import sys
from utils import get_data_path
import plotly.graph_objects as go

notebook_dir = os.path.dirname(os.getcwd())  
project_root = os.path.dirname(notebook_dir) 
sys.path.append(project_root) 

In [55]:
df = pd.read_csv(get_data_path('data/arima/arima_data.csv'))
df['StartDateTime'] = pd.to_datetime(df['StartDateTime'], format='%d/%m/%Y %H:%M')
df.set_index('StartDateTime', inplace=True)

# Check for NaNs and infinite values and fix the freuqncey for the model (used later)
df = df.asfreq('30min')
print("Number of NaNs in data:", df['ISEM DA Price'].isna().sum())
print("Number of infinite values in data:", np.isinf(df['ISEM DA Price']).sum())
df = df[np.isfinite(df['ISEM DA Price'])]

Number of NaNs in data: 0
Number of infinite values in data: 0


### configuration, training, etc blah balh blah

#### Overview
Training: full data split into 80% training and 20% testing segments.
and evulates multiple model configurations for holt-winters ES to select the best forecasting approach.

#### how the code works:
- sMAPE Function: calcs symmetric MAEPE 
- data split: desciberd above
- Model configs: Define the  setups with varying trend types, seasonal components, seasonal periods, and damped trend et cetera.
- Model training & evals. Described below

#### Model training & evals:
- does this by training each config on historical price data.
- Forecasts for the test period.
- Computes RMSE, MAE, and sMAPE to assess model performance.
- Best Model Selection: Identifies the optimal configuration based on the lowest RMSE.

#### Config adjusting:
- Adjust configs: do this by adding lines in the configs list with ur parameters (trend, seasonal, seasonal_periods, damped_trend, and a descriptive name). experiment!

In [56]:
# using sMAPE function
def smape(actual, forecast):
    return 100/len(actual) * np.sum(2 * np.abs(forecast - actual) / (np.abs(actual) + np.abs(forecast)))

# Train/test split. this uses full dataset
train_size = int(len(df) * 0.8)
train = df.iloc[:train_size]
test = df.iloc[train_size:]

print(f"Training data: {len(train)} points ({train.index.min()} to {train.index.max()})")
print(f"Testing data: {len(test)} points ({test.index.min()} to {test.index.max()})")

# Model configurations
configs = [
    {"trend": "add", "seasonal": "add", "seasonal_periods": 48, "damped_trend": True, "name": "Daily Additive + Damped"},
    {"trend": "add", "seasonal": "add", "seasonal_periods": 48, "damped_trend": False, "name": "Daily Additive"},
    {"trend": None, "seasonal": "add", "seasonal_periods": 48, "damped_trend": False, "name": "No Trend + Daily Season"},
    {"trend": "add", "seasonal": "add", "seasonal_periods": 48*7, "damped_trend": True, "name": "Weekly Additive + Damped"},
    {"trend": "add", "seasonal": "add", "seasonal_periods": 48*2, "damped_trend": True, "name": "Two-Day Pattern"}
]

# Train and evaluate models
print("Testing Holt-Winters configurations:")
results = []

try:
    for config in configs:
        try:
            # Skip if not enough data
            if config["seasonal_periods"] > len(train) / 2:
                print(f"Skipping {config['name']} - insufficient data")
                continue
            
            print(f"Fitting {config['name']}...")
            
            model = ExponentialSmoothing(
                train['ISEM DA Price'],
                trend=config["trend"],
                seasonal=config["seasonal"],
                seasonal_periods=config["seasonal_periods"],
                damped_trend=config["damped_trend"]
            ).fit(optimized=True)
            
            # create forecasts
            preds = model.forecast(len(test))
            preds = pd.Series(preds, index=test.index)
            
            # calc metrics
            rmse = np.sqrt(mean_squared_error(test['ISEM DA Price'], preds))
            mae = mean_absolute_error(test['ISEM DA Price'], preds)
            smape_val = smape(test['ISEM DA Price'], preds)
            
            # store results
            results.append({
                "name": config["name"],
                "model": model, 
                "predictions": preds,
                "rmse": rmse,
                "mae": mae,
                "smape": smape_val
            })
            
            print(f"{config['name']}: RMSE={rmse:.2f}, MAE={mae:.2f}, sMAPE={smape_val:.2f}%")
            
        except Exception as e:
            print(f"Error with {config['name']}: {str(e)}")
    
    # Find best model
    if not results:
        print("No successful models.")
        best_model_info = None
    else:
        best_model_info = min(results, key=lambda x: x["rmse"])
        print(f"\nBest model: {best_model_info['name']} (RMSE: {best_model_info['rmse']:.2f})")
        
except Exception as e:
    print(f"Error in modeling process: {str(e)}")
    import traceback
    traceback.print_exc()
    best_model_info = None

Training data: 42048 points (2022-01-22 00:00:00 to 2024-06-15 23:30:00)
Testing data: 10512 points (2024-06-16 00:00:00 to 2025-01-20 23:30:00)
Testing Holt-Winters configurations:
Fitting Daily Additive + Damped...
Daily Additive + Damped: RMSE=66.93, MAE=58.43, sMAPE=49.22%
Fitting Daily Additive...
Daily Additive: RMSE=114.17, MAE=105.24, sMAPE=71.30%
Fitting No Trend + Daily Season...
No Trend + Daily Season: RMSE=66.46, MAE=57.86, sMAPE=48.87%
Fitting Weekly Additive + Damped...
Weekly Additive + Damped: RMSE=57.16, MAE=40.41, sMAPE=48.88%
Fitting Two-Day Pattern...
Two-Day Pattern: RMSE=53.73, MAE=41.91, sMAPE=39.88%

Best model: Two-Day Pattern (RMSE: 53.73)


### plotting 

to teammates: the code is written so that ideally you shouldnt have to touch this box 

In [42]:
if best_model_info:
    # Extract data for plotting
    best_preds = best_model_info["predictions"]
    model_name = best_model_info["name"]
    
    # Create plot
    fig = go.Figure()
    
    # add all training data
    fig.add_trace(go.Scatter(
        x=train.index, 
        y=train['ISEM DA Price'],
        name='Training Data',
        line=dict(color='blue')
    ))
    
    # add all test data (actual values)
    fig.add_trace(go.Scatter(
        x=test.index, 
        y=test['ISEM DA Price'],
        name='Actual Values',
        line=dict(color='green')
    ))
    
    # add all forecasts
    fig.add_trace(go.Scatter(
        x=test.index, 
        y=best_preds,
        name='Forecast',
        line=dict(color='red')
    ))
    
    # layout
    fig.update_layout(
        title=f'Holt-Winters: {model_name}',
        xaxis_title='Date',
        yaxis_title='Price (€/MWh)',
        hovermode='x unified',
        legend=dict(orientation="h", y=1.1)
    )
    
    # range selector. NOTE: ITS GONNA LOOK BAD WHEN YOU LOAD AT FIRST BECAUSE ITS A BIG DATASET. 
    # I solved that problem by adding selectors to make it look better and easier to navigate 
    # or use the slider at the bottom. 
    fig.update_xaxes(
        rangeslider_visible=True,
        rangeselector=dict(
            buttons=list([
                dict(count=1, label="1m", step="month", stepmode="backward"),
                dict(count=3, label="3m", step="month", stepmode="backward"),
                dict(count=6, label="6m", step="month", stepmode="backward"),
                dict(count=1, label="YTD", step="year", stepmode="todate"),
                dict(count=1, label="1y", step="year", stepmode="backward"),
                dict(step="all")
            ])
        )
    )
    
    # Show plot
    fig.show()

### Other Analysis

#### PLOT 1: Residuals Over Time
- Calculation: The difference between actual and predicted prices for each point in the test set. 
- Insight: Shows howe prediction errors change over time. Large spikes suggest the model struggles, especially in winter time

#### PLOT 2: MAE by Hour of Day
- Calculation: Find the average absolute error for each hour of the day (0-23).  
- Insight: thjer are patterns in errors across the day, modul performs better at night (0-6) and worse during peak hours (11-17).

#### PLOT 3: MAE by Price Range
- Calculation: Find the average absolute error for different price ranges (0-50, 50-100, 100-150, >150 €/ mega watt hour)  
- Insight: Shows that the model struggles with very low or very high prices but does well in the middle range. IMO we can fix this by just training on 1 year's worth of data. 

In [58]:
if results:
    # Get best model
    best_model_info = min(results, key=lambda x: x["rmse"])
    
    print("\nBEST MODEL FOUND:")
    print(f"Configuration: {best_model_info['name']}")
    print(f"RMSE: {best_model_info['rmse']:.2f}")
    print(f"MAE: {best_model_info['mae']:.2f}")
    print(f"sMAPE: {best_model_info['smape']:.2f}%")
    
    best_preds = best_model_info["predictions"]
    residuals = test['ISEM DA Price'] - best_preds
    
    # Prepare data for analysis
    test_copy = test.copy()
    test_copy['hour'] = test_copy.index.hour
    test_copy['abs_residual'] = abs(residuals)
    test_copy['price_range'] = pd.cut(test_copy['ISEM DA Price'], 
                                    bins=[0, 50, 100, 150, float('inf')],
                                    labels=['0-50', '50-100', '100-150', '>150'])
    
    # 1. Residuals plot
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=test.index, y=residuals, name='Residuals'))
    fig.add_shape(type="line", x0=test.index[0], y0=0, x1=test.index[-1], y1=0, 
                 line=dict(color="red", width=2, dash="dash"))
    fig.update_layout(title='Residuals Over Time', xaxis_title='Date', 
                     yaxis_title='Residual (Actual - Predicted)')
    fig.show()
    
    # 2. Error by hour
    hourly_error = test_copy.groupby('hour', observed=True)['abs_residual'].mean()
    fig = go.Figure(data=[go.Bar(x=hourly_error.index, y=hourly_error.values)])
    fig.update_layout(title='Mean Absolute Error by Hour of Day', 
                     xaxis_title='Hour', yaxis_title='Mean Absolute Error',
                     xaxis=dict(tickmode='linear', tick0=0, dtick=1))
    fig.show()
    
    # 3. Error by price range
    price_range_error = test_copy.groupby('price_range', observed=True)['abs_residual'].mean()
    fig = go.Figure(data=[go.Bar(x=price_range_error.index, y=price_range_error.values)])
    fig.update_layout(title='Mean Absolute Error by Price Range',
                     xaxis_title='Price Range (€/MWh)', yaxis_title='Mean Absolute Error')
    fig.show()


BEST MODEL FOUND:
Configuration: Two-Day Pattern
RMSE: 53.73
MAE: 41.91
sMAPE: 39.88%
